In [ ]:
import numpy as np # linear algebra
import pandas as pd # data processing, CSV file I/O (e.g. pd.read_csv)

# Input data files are available in the read-only "../input/" directory
# For example, running this (by clicking run or pressing Shift+Enter) will list all files under the input directory

import os
# for dirname, _, filenames in os.walk('/kaggle/input'):
#     for filename in filenames:
#         print(os.path.join(dirname, filename))

In [ ]:
data=pd.read_csv("/content/sample_data/mnist_test.csv")

In [ ]:
data.head()

7  0  0.1  0.2  0.3  0.4  0.5  0.6  0.7  0.8  ...  0.658  0.659  0.660  \
0  2  0    0    0    0    0    0    0    0    0  ...      0      0      0   
1  1  0    0    0    0    0    0    0    0    0  ...      0      0      0   
2  0  0    0    0    0    0    0    0    0    0  ...      0      0      0   
3  4  0    0    0    0    0    0    0    0    0  ...      0      0      0   
4  1  0    0    0    0    0    0    0    0    0  ...      0      0      0   

   0.661  0.662  0.663  0.664  0.665  0.666  0.667  
0      0      0      0      0      0      0      0  
1      0      0      0      0      0      0      0  
2      0      0      0      0      0      0      0  
3      0      0      0      0      0      0      0  
4      0      0      0      0      0      0      0  

[5 rows x 785 columns]

In [ ]:
!pip install git+https://github.com/openai/CLIP.git

  Cloning https://github.com/openai/CLIP.git to /tmp/pip-req-build-psbbvg30
  Running command git clone --filter=blob:none --quiet https://github.com/openai/CLIP.git /tmp/pip-req-build-psbbvg30
  Resolved https://github.com/openai/CLIP.git to commit a1d071733d7111c9c014f024669f959182114e33
  Preparing metadata (setup.py) ... done
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 54.4/54.4 kB 1.8 MB/s eta 0:00:00
  Using cached nvidia_cuda_nvrtc_cu12-12.1.105-py3-none-manylinux1_x86_64.whl (23.7 MB)
  Using cached nvidia_cuda_runtime_cu12-12.1.105-py3-none-manylinux1_x86_64.whl (823 kB)
  Using cached nvidia_cuda_cupti_cu12-12.1.105-py3-none-manylinux1_x86_64.whl (14.1 MB)
  Using cached nvidia_cudnn_cu12-8.9.2.26-py3-none-manylinux1_x86_64.whl (731.7 MB)
  Using cached nvidia_cublas_cu12-12.1.3.1-py3-none-manylinux1_x86_64.whl (410.6 MB)
  Using cached nvidia_cufft_cu12-11.0.2.54-py3-none-manylinux1_x86_64.whl (121.6 MB)
  Using cached nvidia_curand_cu12-10.3.2.106-py3-none-manylinux1_x86_

In [ ]:
from PIL import Image
from io import BytesIO
import torch
from transformers import CLIPProcessor, CLIPModel
import clip

device= "cuda" if torch.cuda.is_available() else "cpu"

#model,preprocess=clip.load("ViT-B/32", device=device)

model=CLIPModel.from_pretrained("openai/clip-vit-base-patch32").to("cpu")
processor=CLIPProcessor.from_pretrained("openai/clip-vit-base-patch32")

/usr/local/lib/python3.10/dist-packages/huggingface_hub/utils/_token.py:89: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(


config.json:   0%|          | 0.00/4.19k [00:00<?, ?B/s]

pytorch_model.bin:   0%|          | 0.00/605M [00:00<?, ?B/s]

preprocessor_config.json:   0%|          | 0.00/316 [00:00<?, ?B/s]

tokenizer_config.json:   0%|          | 0.00/592 [00:00<?, ?B/s]

vocab.json:   0%|          | 0.00/862k [00:00<?, ?B/s]

merges.txt:   0%|          | 0.00/525k [00:00<?, ?B/s]

tokenizer.json:   0%|          | 0.00/2.22M [00:00<?, ?B/s]

special_tokens_map.json:   0%|          | 0.00/389 [00:00<?, ?B/s]

In [ ]:
import torch
import torchvision.transforms as transforms
import torchvision.datasets as datasets
from torch.utils.data import DataLoader, Subset

In [ ]:
transform = transforms.Compose([
    transforms.Grayscale(3),
    transforms.Resize((224, 224)),
    transforms.ToTensor()
])

In [ ]:
mnist_dataset = datasets.MNIST(root='./data', train=True, download=True, transform=transform)

In [ ]:
limited_mnist_dataset = Subset(mnist_dataset, range(500))

In [ ]:
mnist_loader = DataLoader(limited_mnist_dataset, batch_size=32, shuffle=False)

In [ ]:
limited_data1 = data[:500]

In [ ]:
image_embeddings = []

from tqdm import tqdm


for images, _ in tqdm(mnist_loader, desc="Processing images"):
    inputs = processor(images=images, return_tensors="pt", do_rescale=False).to("cpu")
    with torch.no_grad():
        image_embedding = model.get_image_features(**inputs)
    image_embeddings.append(image_embedding.cpu().numpy())


image_embeddings = np.concatenate(image_embeddings, axis=0)
np.save("mnist_image_embeddings.npy", image_embeddings)
print("Shape:", image_embeddings[1].shape)

Processing images: 100%|██████████| 16/16 [01:32<00:00,  5.80s/it]

Shape of image embeddings: (512,)


In [ ]:
import numpy as np
from sklearn.decomposition import PCA

In [ ]:
pca=PCA(n_components=3)
#pca_embeddings=pca.fit_transform(flat_image_embeddings_2d)
pca_embeddings=pca.fit_transform(image_embeddings)

In [ ]:
len(pca_embeddings)

500

In [ ]:
import plotly.express as px

import base64

mnist_subset = torch.utils.data.Subset(mnist_dataset, range(500))

def encode_image(image_tensor):
    pil_image = transforms.ToPILImage()(image_tensor)
    buffer = BytesIO()
    pil_image.save(buffer, format="PNG")
    encoded_image = base64.b64encode(buffer.getvalue()).decode('utf-8')
    return encoded_image

images_subset = [image for image, _ in mnist_subset]

encoded_images = [encode_image(image) for image in images_subset]

html_strings = ['<img src="data:image/png;base64,{}" style="width:50px">'.format(enc_img) for enc_img in encoded_images]



In [ ]:
subset_class_labels = limited_mnist_dataset.dataset.targets[limited_mnist_dataset.indices]
num_classes_subset = len(subset_class_labels.unique())
print("Number of different classes in the subset:", num_classes_subset)

Number of different classes in the subset: 10


In [ ]:
df_pca = pd.DataFrame({
    'x': pca_embeddings[:, 0],
    'y': pca_embeddings[:, 1],
    'z': pca_embeddings[:, 2],
    'class_label': subset_class_labels,
    'html_img': html_strings
})

fig_pca = px.scatter_3d(df_pca, x='x', y='y', z='z', color='class_label', hover_data=['html_img'])
fig_pca.update_traces(marker=dict(size=5))
fig_pca.show()

In [ ]:
!pip install umap-learn

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 85.7/85.7 kB 2.1 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 56.8/56.8 kB 6.9 MB/s eta 0:00:00


In [ ]:
subset_class_labels = limited_mnist_dataset.dataset.targets[limited_mnist_dataset.indices]
umap_embeddings = UMAP(n_components=3).fit_transform(image_embeddings)
df_umap = pd.DataFrame({
    'x': umap_embeddings[:, 0],
    'y': umap_embeddings[:, 1],
    'z': umap_embeddings[:, 2],
    'class_label': subset_class_labels
})

fig_umap = px.scatter_3d(df_umap, x='x', y='y', z='z', color='class_label')
fig_umap.update_traces(marker=dict(size=5))
fig_umap.show()